In [4]:
import tweepy

In [5]:
# Fill the X's with the appropriate credentials
consumer_key = "VioRnG1RsP4QIjpgEaycSHa6Z" 
consumer_secret = "FtrF8arPLGfvkBenBgD1dz8aqzqimHaGkyqvyF2t4y95ytPJLL"
access_key = "827571463704150022-qzKIUif3a1g8fCEolzrThlnyVaK14aD"
access_secret = "WDAwvVmm4W00t98orVZB2j8HLAOskEjcs84k0O68s41jL"

In [6]:
# Authorization to consumer key and consumer secret 
auth = tweepy.OAuthHandler(consumer_key, consumer_secret) 

# Access to user's access key and access secret 
auth.set_access_token(access_key, access_secret) 

# Calling api 
api = tweepy.API(auth) 

username = 'midasIIITD'


In [23]:
def get_all_tweets(screen_name,api,auth):
    # Twitter only allows access to a users most recent 3240 tweets with this method


    # initialize a list to hold all the tweepy Tweets
    alltweets = []

    # make initial request for most recent tweets (200 is the maximum allowed count)
    new_tweets = api.user_timeline(screen_name = screen_name,count=199)

    # save most recent tweets
    alltweets.extend(new_tweets)

    # save the id of the oldest tweet less one
    oldest = alltweets[-1].id - 1

    # keep grabbing tweets until there are no tweets left to grab
    while len(new_tweets) > 0:

        #all subsiquent requests use the max_id param to prevent duplicates
        new_tweets = api.user_timeline(screen_name = screen_name,count=199,max_id=oldest,tweet_mode="extended",include_entities=True)

        #save most recent tweets
        alltweets.extend(new_tweets)

        #update the id of the oldest tweet less one
        oldest = alltweets[-1].id - 1

    # print total tweets fetched from given screen name
    print("Total tweets downloaded from %s are %s" % (screen_name,len(alltweets)))

    return alltweets

get_all_tweets(username,api,auth)

Total tweets downloaded from midasIIITD are 342


[Status(_api=<tweepy.api.API object at 0x000001D3BA05DEB8>, _json={'created_at': 'Tue Apr 09 16:45:07 +0000 2019', 'id': 1115656899892879361, 'id_str': '1115656899892879361', 'text': 'RT @IIITDelhi: We are delighted to share that IIIT-Delhi is ranked 55 by NIRF this year. We have moved up by 11 positions compared to the p…', 'truncated': False, 'entities': {'hashtags': [], 'symbols': [], 'user_mentions': [{'screen_name': 'IIITDelhi', 'name': 'IIIT Delhi', 'id': 2227868629, 'id_str': '2227868629', 'indices': [3, 13]}], 'urls': []}, 'source': '<a href="http://twitter.com" rel="nofollow">Twitter Web Client</a>', 'in_reply_to_status_id': None, 'in_reply_to_status_id_str': None, 'in_reply_to_user_id': None, 'in_reply_to_user_id_str': None, 'in_reply_to_screen_name': None, 'user': {'id': 1021355762575073281, 'id_str': '1021355762575073281', 'name': 'MIDAS IIITD', 'screen_name': 'midasIIITD', 'location': 'New Delhi, India', 'description': 'MIDAS is a group of researchers at IIIT-Delhi who stu

In [25]:
import json
#Dumping tweets data to JSON file.

def dump_to_json(alltweets,fname):

    for i in range(len(alltweets)):

        
        alltweets[i] = alltweets[i]._json
        
    with open(fname, 'w',encoding='utf8') as file:
        json.dump(alltweets, file,indent = 4)
    
    print('Tweets dumped')


alltweets = get_all_tweets(username,api,auth)

fname = 'tweets.json'
dump_to_json(alltweets,fname)

Total tweets downloaded from midasIIITD are 342
Tweets dumped


In [ ]:
import pandas as pd
import json
#parsing JSON dump to extract info

def get_num_of_imgs_in_tweet(tweet):
    #returns num of imgs in a tweet
    #if no imgs return None.

    media = tweet['entities'].get('media',[])
    
    if len(media) > 0:
        
        #filtering photo out of other types of media
        imgs = list(filter(lambda x: x['type']=='photo', media))
        print(imgs)
        
        return len(imgs)
        
    else:
        return None
     
    
    
    
    
    
def extract_info_from_tweets(fname,tweets_info):
    
    with open(fname, 'r',encoding='utf8') as file:
            
        alltweets = json.load(file)
            
        for tweet in alltweets:

            tweet_info_dict = {}

            #extract tweet id
            tweet_id = tweet['id_str']
            print('tweet_id',tweet_id)
            tweet_info_dict['tweet_id'] = tweet_id

            #extract tweet text
            tweet_text = tweet.get('text','')
            
            #in some tweets the key 'full_text' holds
            #the text of the tweet instead of 'text'
            if tweet_text == '':
                tweet_text = tweet['full_text']
                
            print('tweet_text',tweet_text)
            tweet_info_dict['tweet_text'] = tweet_text

            #extract tweet datetime
            tweet_datetime = tweet['created_at']
            print('tweet_datetime',tweet_datetime)
            tweet_info_dict['tweet_datetime'] = tweet_datetime

            #extract num of favorites
            tweet_favorite_count = tweet['favorite_count']
            print('tweet_favorite_count',tweet_favorite_count)
            tweet_info_dict['tweet_favorite_count'] = tweet_favorite_count

            #extract num of retweets
            tweet_retweet_count = tweet['retweet_count']
            print('tweet_retweet_count',tweet_retweet_count)
            tweet_info_dict['tweet_retweet_count'] = tweet_retweet_count

            #extract num of images
            tweet_imgs_count = get_num_of_imgs_in_tweet(tweet)
            print('tweet_imgs_count',tweet_imgs_count)
            tweet_info_dict['tweet_imgs_count'] = tweet_imgs_count

            print(tweet_info_dict)
            print('*'*40)

            tweets_info.append(tweet_info_dict)
            
    df = pd.DataFrame(tweets_info)
    return df
            
        
                
                
                

            
                
            
fname = 'tweets.json'       
df = extract_info_from_tweets(fname,[])
print(df)